In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from bs4 import BeautifulSoup
import re
import requests
%config InlineBackend.figure_formats = ['svg']
%matplotlib inline

sns.set(context='notebook', style='whitegrid', font_scale=1.2)

## Getting a dataframe of top 1000 movies with worldwide lifetime gross

In [2]:
url1 = 'https://www.boxofficemojo.com/chart/ww_top_lifetime_gross/?area=XWW' 
url2 = 'https://www.boxofficemojo.com/chart/ww_top_lifetime_gross/?area=XWW&offset=200'
url3 = 'https://www.boxofficemojo.com/chart/ww_top_lifetime_gross/?area=XWW&offset=400'
url4 = 'https://www.boxofficemojo.com/chart/ww_top_lifetime_gross/?area=XWW&offset=600'
url5 = 'https://www.boxofficemojo.com/chart/ww_top_lifetime_gross/?area=XWW&offset=800'
url_list = [url1, url2, url3, url4, url5]

movies_dict = {}
for url in url_list:
    response = requests.get(url)
    page = response.text
    soup = BeautifulSoup(page, "lxml")
    table = soup.find('table')
    rows = [row for row in table.find_all('tr')]

    for row in rows[1:]:
        items = row.find_all('td')
        link = items[1].find('a')
        title, url = link.text, link['href']
        movies_dict[title] = [url] + [i.text for i in items[1:]]

In [3]:
movies_df = pd.DataFrame(movies_dict).T  #transpose
movies_df.columns = ['link_stub', 'title', 'World Lifetime Gross', 
                    'Domestic Lifetime Gross', 'Domestic %', 
                    'Foreign Lifetime Gross', 'Foreign %', 'year']

movies_df

link_stub  \
Avatar                                        /title/tt0499549/?ref_=bo_cso_table_1   
Avengers: Endgame                             /title/tt4154796/?ref_=bo_cso_table_2   
Titanic                                       /title/tt0120338/?ref_=bo_cso_table_3   
Star Wars: Episode VII - The Force Awakens    /title/tt2488496/?ref_=bo_cso_table_4   
Avengers: Infinity War                        /title/tt4154756/?ref_=bo_cso_table_5   
...                                                                             ...   
Cold Mountain                               /title/tt0159365/?ref_=bo_cso_table_196   
Black Hawk Down                             /title/tt0265086/?ref_=bo_cso_table_197   
The Grand Budapest Hotel                    /title/tt2278388/?ref_=bo_cso_table_198   
The Santa Clause 2                          /title/tt0304669/?ref_=bo_cso_table_199   
Cloverfield                                 /title/tt1060277/?ref_=bo_cso_table_200   

                                                                                 title  \
Avatar                                                                          Avatar   
Avengers: Endgame                                                    Avengers: Endgame   
Titanic                                                                        Titanic   
Star Wars: Episode VII - The Force Awakens  Star Wars: Episode VII - The Force Awakens   
Avengers: Infinity War                                          Avengers: Infinity War   
...                                                                                ...   
Cold Mountain                                                            Cold Mountain   
Black Hawk Down                                                        Black Hawk Down   
The Grand Budapest Hotel                                      The Grand Budapest Hotel   
The Santa Clause 2                                                  The Santa Clause 2   
Cloverfield                                                                Cloverfield   

                                           World Lifetime Gross  \
Avatar                                           $2,847,246,203   
Avengers: Endgame                                $2,797,501,328   
Titanic                                          $2,201,647,264   
Star Wars: Episode VII - The Force Awakens       $2,069,521,700   
Avengers: Infinity War                           $2,048,359,754   
...                                                         ...   
Cold Mountain                                      $173,013,509   
Black Hawk Down                                    $172,989,651   
The Grand Budapest Hotel                           $172,945,750   
The Santa Clause 2                                 $172,855,065   
Cloverfield                                        $172,394,180   

                                           Domestic Lifetime Gross Domestic %  \
Avatar                                                $760,507,625      26.7%   
Avengers: Endgame                                     $858,373,000      30.7%   
Titanic                                               $659,363,944        30%   
Star Wars: Episode VII - The Force Awakens            $936,662,225      45.3%   
Avengers: Infinity War                                $678,815,482      33.1%   
...                                                            ...        ...   
Cold Mountain                                          $95,636,509      55.3%   
Black Hawk Down                                       $108,638,745      62.8%   
The Grand Budapest Hotel                               $59,301,324      34.3%   
The Santa Clause 2                                    $139,236,327      80.6%   
Cloverfield                                            $80,048,433      46.4%   

                                           Foreign Lifetime Gross Foreign %  \
Avatar                                             $2,086,738,578     73.3%   
Avengers: En

### Function getting movie values

In [4]:
def get_movie_value(soup, field_name):
    
    '''Grab a value from Box Office Mojo HTML
    
    Takes a string attribute of a movie on the page and returns the string in
    the next sibling object (the value for that attribute) or None if nothing is found.
    '''
    
    obj = soup.find(text=re.compile(field_name))
    
    if not obj: 
        return None
    
    # this works for most of the values
    next_element = obj.findNext()
    
    if next_element:
        return next_element.text 
    else:
        return None

### All useful functions to clean data

In [5]:
import dateutil.parser

def money_to_int(moneystring):
    moneystring = moneystring.replace('$', '').replace(',', '').replace('-','')
    try:
        return int(moneystring)
    except ValueError:
        return 0

def runtime_to_minutes(runtimestring):
    runtime = runtimestring.split()
    try:
        minutes = int(runtime[0])*60 + int(runtime[2])
        return minutes
    except:
        return 0

def to_date(datestring):
    date = dateutil.parser.parse(datestring)
    return date

### Getting all movie items from each movie page into the dataframe

In [6]:
def get_movie_items(row):
    base_url = 'https://www.boxofficemojo.com'
    
    #Create full url to scrape
    url = base_url + row['link_stub']
    
    #Request HTML and parse
    response = requests.get(url)
    page = response.text
    soup = BeautifulSoup(page,"lxml")
    
    #Getting domestic distributor
    try:
        row['Domestic Distributor'] = (get_movie_value(soup,'Domestic Distributor')
                                       .replace('See full company information',''))
    except AttributeError:
        row['Domestic Distributor'] = ''
        
    
    #Getting domestic opening
    try:
        row['Domestic Opening'] = money_to_int(get_movie_value(soup,'Domestic Opening'))
    except AttributeError:
        row['Domestic Opening'] = 0
    
    #Getting budget
    try:
        budget = get_movie_value(soup,'Budget')
        row['budget'] = money_to_int(budget)
    except AttributeError:
        row['budget'] = 0
    
    #Getting MPAA rating
    try:
        row['MPAA'] = get_movie_value(soup,'MPAA')
    except AttributeError:
        row['MPAA'] = ''
        
    #Getting running time
    try:
        row['Running Time'] = runtime_to_minutes(get_movie_value(soup,'Run'))
    except AttributeError:
        row['Running Time'] = 0
    
    #Getting genres
    try:
        genres = (get_movie_value(soup,'Genres').replace(' ','')
                  .replace('\n','').replace('Sci-Fi','Science fiction'))
        row['genres'] = re.findall('[A-Z][^A-Z]*', genres)
    except AttributeError:
        row['genres'] = ''
    
    ##Getting Original Release values
    if (soup.find_all('h3')[0].text == 'By Release'):
        original_release_domestic = soup.find('table').find_all('td')[3].text
        row['Original Release Domestic'] = money_to_int(original_release_domestic)
        original_release_international = soup.find('table').find_all('td')[4].text
        row['Original Release International'] = money_to_int(original_release_international)
        original_release_worldwide = soup.find('table').find_all('td')[5].text
        row['Original Release Worldwide'] = money_to_int(original_release_worldwide)
    else:
        row['Original Release Domestic'] = money_to_int(row['Domestic Lifetime Gross'])
        row['Original Release International'] = money_to_int(row['Foreign Lifetime Gross'])
        row['Original Release Worldwide'] = money_to_int(row['World Lifetime Gross'])
        
    return row

In [7]:
movies_df = movies_df.apply(get_movie_items, axis = 1)

In [8]:
movies_df

link_stub  \
Avatar                                        /title/tt0499549/?ref_=bo_cso_table_1   
Avengers: Endgame                             /title/tt4154796/?ref_=bo_cso_table_2   
Titanic                                       /title/tt0120338/?ref_=bo_cso_table_3   
Star Wars: Episode VII - The Force Awakens    /title/tt2488496/?ref_=bo_cso_table_4   
Avengers: Infinity War                        /title/tt4154756/?ref_=bo_cso_table_5   
...                                                                             ...   
Cold Mountain                               /title/tt0159365/?ref_=bo_cso_table_196   
Black Hawk Down                             /title/tt0265086/?ref_=bo_cso_table_197   
The Grand Budapest Hotel                    /title/tt2278388/?ref_=bo_cso_table_198   
The Santa Clause 2                          /title/tt0304669/?ref_=bo_cso_table_199   
Cloverfield                                 /title/tt1060277/?ref_=bo_cso_table_200   

                                                                                 title  \
Avatar                                                                          Avatar   
Avengers: Endgame                                                    Avengers: Endgame   
Titanic                                                                        Titanic   
Star Wars: Episode VII - The Force Awakens  Star Wars: Episode VII - The Force Awakens   
Avengers: Infinity War                                          Avengers: Infinity War   
...                                                                                ...   
Cold Mountain                                                            Cold Mountain   
Black Hawk Down                                                        Black Hawk Down   
The Grand Budapest Hotel                                      The Grand Budapest Hotel   
The Santa Clause 2                                                  The Santa Clause 2   
Cloverfield                                                                Cloverfield   

                                           World Lifetime Gross  \
Avatar                                           $2,847,246,203   
Avengers: Endgame                                $2,797,501,328   
Titanic                                          $2,201,647,264   
Star Wars: Episode VII - The Force Awakens       $2,069,521,700   
Avengers: Infinity War                           $2,048,359,754   
...                                                         ...   
Cold Mountain                                      $173,013,509   
Black Hawk Down                                    $172,989,651   
The Grand Budapest Hotel                           $172,945,750   
The Santa Clause 2                                 $172,855,065   
Cloverfield                                        $172,394,180   

                                           Domestic Lifetime Gross Domestic %  \
Avatar                                                $760,507,625      26.7%   
Avengers: Endgame                                     $858,373,000      30.7%   
Titanic                                               $659,363,944        30%   
Star Wars: Episode VII - The Force Awakens            $936,662,225      45.3%   
Avengers: Infinity War                                $678,815,482      33.1%   
...                                                            ...        ...   
Cold Mountain                                          $95,636,509      55.3%   
Black Hawk Down                                       $108,638,745      62.8%   
The Grand Budapest Hotel                               $59,301,324      34.3%   
The Santa Clause 2                                    $139,236,327      80.6%   
Cloverfield                                            $80,048,433      46.4%   

                                           Foreign Lifetime Gross Foreign %  \
Avatar                                             $2,086,738,578     73.3%   
Avengers: En

In [9]:
movies_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 990 entries, Avatar to Cloverfield
Data columns (total 17 columns):
 #   Column                          Non-Null Count  Dtype 
---  ------                          --------------  ----- 
 0   link_stub                       990 non-null    object
 1   title                           990 non-null    object
 2   World Lifetime Gross            990 non-null    object
 3   Domestic Lifetime Gross         990 non-null    object
 4   Domestic %                      990 non-null    object
 5   Foreign Lifetime Gross          990 non-null    object
 6   Foreign %                       990 non-null    object
 7   year                            990 non-null    object
 8   Domestic Distributor            990 non-null    object
 9   Domestic Opening                990 non-null    int64 
 10  budget                          990 non-null    int64 
 11  MPAA                            869 non-null    object
 12  Running Time                    990 non-nu

In [10]:
sns.pairplot(movies_df)

In [12]:
movies_df.to_csv('movies_df.csv', index = False)

In [14]:
movies_df.shape

(990, 17)

In [21]:
movies_df.astype(bool).sum(axis=0)

link_stub                         990
title                             990
World Lifetime Gross              990
Domestic Lifetime Gross           990
Domestic %                        990
Foreign Lifetime Gross            990
Foreign %                         990
year                              990
Domestic Distributor              969
Domestic Opening                  960
budget                            805
MPAA                              869
Running Time                      964
genres                            990
Original Release Domestic         968
Original Release International    920
Original Release Worldwide        990
dtype: int64